In [1]:
import pandas as pd
import plotly.graph_objects as go
import numpy as np

In [2]:
df_solar = pd.read_csv("D:/Users/paulh/Desktop/Domäneprojekt2/Energy_production_price_prediction/HEFTcom24/data/solar1.csv")

In [6]:
df_solar.drop(columns=['Unnamed: 0','boa_MWh','Wind_MW','Wind_MWh_credit'], inplace=True)
df_solar.valid_time = pd.to_datetime(df_solar.valid_time) 
df_solar.reference_time = pd.to_datetime(df_solar.reference_time)
df_solar = df_solar.groupby("valid_time").last().reset_index()

In [9]:
df_solar.dropna(inplace=True)

In [10]:
df_solar

valid_time            reference_time  \
0     2020-09-20 00:00:00+00:00 2020-09-20 00:00:00+00:00   
1     2020-09-20 00:30:00+00:00 2020-09-20 00:00:00+00:00   
2     2020-09-20 01:00:00+00:00 2020-09-20 00:00:00+00:00   
3     2020-09-20 01:30:00+00:00 2020-09-20 00:00:00+00:00   
4     2020-09-20 02:00:00+00:00 2020-09-20 00:00:00+00:00   
...                         ...                       ...   
50930 2023-08-25 23:30:00+00:00 2023-08-24 00:00:00+00:00   
50931 2023-08-26 00:00:00+00:00 2023-08-24 00:00:00+00:00   
50932 2023-08-26 00:30:00+00:00 2023-08-24 00:00:00+00:00   
50933 2023-08-26 01:00:00+00:00 2023-08-24 00:00:00+00:00   
50934 2023-08-26 01:30:00+00:00 2023-08-24 00:00:00+00:00   

       CloudCover_Point0_dwd  CloudCover_Point1_dwd  CloudCover_Point2_dwd  \
0                   0.426270               0.647109               0.335176   
1                   0.435937               0.637988               0.404287   
2                   0.445605               0.628867               0.473398   
3                   0.486719               0.649297               0.523574   
4                   0.527832               0.669727               0.573750   
...                      ...                    ...                    ...   
50930               0.912051               0.548457               0.567803   
50931               0.897656               0.611582               0.493672   
50932               0.901221               0.755117               0.433037   
50933               0.904785               0.898652               0.372402   
50934               0.895713               0.860498               0.279141   

       CloudCover_Point3_dwd  CloudCover_Point4_dwd  CloudCover_Point5_dwd  \
0                   0.652109               0.333633               0.324512   
1                   0.652783               0.346943               0.413809   
2                   0.653457               0.360254               0.503105   
3                   0.652783               0.363057               0.717480   
4                   0.652109               0.365859               0.931855   
...                      ...                    ...                    ...   
50930               0.406289               0.458057               0.363867   
50931               0.379238               0.429512               0.420957   
50932               0.254766               0.450410               0.438418   
50933               0.130293               0.471309               0.455879   
50934               0.065146               0.646621               0.506309   

       CloudCover_Point6_dwd  CloudCover_Point7_dwd  ...  \
0                   0.551094               0.427949  ...   
1                   0.551855               0.438965  ...   
2                   0.552617               0.449980  ...   
3                   0.600264               0.453193  ...   
4                   0.647910               0.456406  ...   
...                      ...                    ...  ...   
50930               0.543496               0.666543  ...   
50931               0.452754               0.702344  ...   
50932               0.612519               0.708125  ...   
50933               0.772285               0.713906  ...   
50934               0.586768               0.650703  ...   

       Temperature_Point18_ncep  Temperature_Point19_ncep  \
0                     16.050018                 12.750000   
1                     16.007080                 12.692078   
2                     15.964142                 12.634155   
3                     15.964859                 12.604874   
4                     15.965576                 12.575592   
...                         ...                       ...   
50930                 15.960434                 12.210434   
50931                 15.861084                 11.961090   
50932                 15.329407                 11.729416   
50933                 14.797730                 11.497742   
50934                 

In [11]:
df_solar['Mean_SolarRadiation_dwd'] = df_solar[[f'SolarDownwardRadiation_Point{i}_dwd' for i in range(20)]].mean(axis=1)
df_solar['Mean_Temperature_dwd'] = df_solar[[f'Temperature_Point{i}_dwd' for i in range(7)]].mean(axis=1)
df_solar['Std_Temperature_dwd'] = df_solar[[f'Temperature_Point{i}_dwd' for i in range(7)]].std(axis=1)

In [17]:
df_solar["Estimated_SolarPower"] = df_solar["Mean_SolarRadiation_dwd"]

In [18]:
#compare Estimated_SolarPower with Solar_MWh_credit with plot and absolute error
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_solar.valid_time, y=df_solar.Estimated_SolarPower, mode='lines', name='Estimated_SolarPower'))
fig.add_trace(go.Scatter(x=df_solar.valid_time, y=df_solar.Solar_MWh_credit, mode='lines', name='Solar_MWh_credit'))
fig.update_layout(title='Estimated SolarPower vs Solar_MWh_credit', xaxis_title='Time', yaxis_title='MWh')
fig.show()

df_solar["Error"] = np.abs(df_solar.Estimated_SolarPower - df_solar.Solar_MWh_credit)
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_solar.valid_time, y=df_solar.Error, mode='lines', name='Error'))
fig.update_layout(title='Error between Estimated SolarPower and Solar_MWh_credit', xaxis_title='Time', yaxis_title='MWh')
fig.show()
